In [2]:
import json
import pandas as pd
import numpy as np
import json
import seaborn as sns
import datetime
import matplotlib.pyplot as plt
from joblib import dump, load
from sklearn.metrics import classification_report, confusion_matrix, accuracy_score
from sklearn.preprocessing import StandardScaler, PowerTransformer
from sklearn.decomposition import PCA
from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestClassifier
from mlxtend.plotting import plot_decision_regions

In [3]:
def load_tmdb_movies(path):
    df = pd.read_csv(path, parse_dates=['release_date'])
    df['release_date'] = pd.to_datetime(df['release_date']).apply(lambda x: x.date())
    json_columns = ['genres', 'keywords', 'production_countries', 'production_companies', 'spoken_languages']
    for column in json_columns:
        df[column] = df[column].apply(json.loads)
    return df

In [4]:
def load_tmdb_credits(path):
    df = pd.read_csv(path)
    json_columns = ['cast', 'crew']
    for column in json_columns:
        df[column] = df[column].apply(json.loads)
    return df

In [5]:
LOST_COLUMNS = [
    'actor_1_facebook_likes',
    'actor_2_facebook_likes',
    'actor_3_facebook_likes',
    'aspect_ratio',
    'cast_total_facebook_likes',
    'color',
    'content_rating',
    'director_facebook_likes',
    'facenumber_in_poster',
    'movie_facebook_likes',
    'movie_imdb_link',
    'num_critic_for_reviews',
    'num_user_for_reviews'
                ]

In [6]:
TMDB_TO_IMDB_SIMPLE_EQUIVALENCIES = {
    'budget': 'budget',
    'genres': 'genres',
    'revenue': 'gross',
    'title': 'movie_title',
    'runtime': 'duration',
    'original_language': 'language',  # it's possible that spoken_languages would be a better match
    'keywords': 'plot_keywords',
    'vote_count': 'num_voted_users',
                                         }

IMDB_COLUMNS_TO_REMAP = {'imdb_score': 'vote_average'}

In [7]:
def safe_access(container, index_values):
    # return a missing value rather than an error upon indexing/key failure
    result = container
    try:
        for idx in index_values:
            result = result[idx]
        return result
    except IndexError or KeyError:
        return pd.np.nan

In [8]:
def get_director(crew_data):
    directors = [x['name'] for x in crew_data if x['job'] == 'Director']
    return safe_access(directors, [0])

In [9]:
def get_companies(company_data):
    companies = [x['name'] for x in company_data if x['name'] == 'Director']
    return safe_access(directors, [0])

In [10]:
def pipe_flatten_names(keywords):
    return '|'.join([x['name'] for x in keywords])

In [11]:
def convert_to_original_format(movies, credits):
    # Converts TMDb data to make it as compatible as possible with kernels built on the original version of the data.
    tmdb_movies = movies.copy()
    tmdb_movies.rename(columns=TMDB_TO_IMDB_SIMPLE_EQUIVALENCIES, inplace=True)
    tmdb_movies['title_year'] = pd.to_datetime(tmdb_movies['release_date']).apply(lambda x: x.year)
    # I'm assuming that the first production country is equivalent, but have not been able to validate this
    tmdb_movies['country'] = tmdb_movies['production_countries'].apply(lambda x: safe_access(x, [0, 'name']))
    tmdb_movies['company'] = tmdb_movies['production_companies'].apply(lambda x: safe_access(x, [0, 'name']))
    tmdb_movies['language'] = tmdb_movies['spoken_languages'].apply(lambda x: safe_access(x, [0, 'name']))
    # tmdb_movies['production_companies'] = tmdb_movies['production_companies'].apply(lambda x: safe_access(x, [0, 'name']))
    tmdb_movies['director_name'] = credits['crew'].apply(get_director)
    tmdb_movies['actor_1_name'] = credits['cast'].apply(lambda x: safe_access(x, [0, 'name']))
    tmdb_movies['actor_2_name'] = credits['cast'].apply(lambda x: safe_access(x, [1, 'name']))
    tmdb_movies['actor_3_name'] = credits['cast'].apply(lambda x: safe_access(x, [2, 'name']))
    tmdb_movies['genres'] = tmdb_movies['genres'].apply(pipe_flatten_names)
    tmdb_movies['plot_keywords'] = tmdb_movies['plot_keywords'].apply(pipe_flatten_names)
    return tmdb_movies

In [12]:
movies = load_tmdb_movies("Data/Original/tmdb_5000_movies.csv")
credits = load_tmdb_credits("Data/tmdb_5000_credits.csv")
original_format = convert_to_original_format(movies, credits)
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', 5)
original_format

budget                                    genres  \
0     237000000  Action|Adventure|Fantasy|Science Fiction   
1     300000000                  Adventure|Fantasy|Action   
...         ...                                       ...   
4801          0                                             
4802          0                               Documentary   

                                          homepage      id  \
0                      http://www.avatarmovie.com/   19995   
1     http://disney.go.com/disneypictures/pirates/     285   
...                                            ...     ...   
4801                   http://shanghaicalling.com/  126186   
4802                                           NaN   25975   

                                          plot_keywords language  \
0     culture clash|future|space war|space colony|so...  English   
1     ocean|drug abuse|exotic island|east india trad...  English   
...                                                 ...      ...   
4801                                                     English   
4802               obsession|camcorder|crush|dream girl  English   

                                original_title  \
0                                       Avatar   
1     Pirates of the Caribbean: At World's End   
...                                        ...   
4801                          Shanghai Calling   
4802                         My Date with Drew   

                                               overview  popularity  \
0     In the 22nd century, a paraplegic Marine is di...  150.437577   
1     Captain Barbossa, long believed to be dead, ha...  139.082615   
...                                                 ...         ...   
4801  When ambitious New York attorney Sam is sent t...    0.857008   
4802  Ever since the second grade when he first saw ...    1.929883   

                                   production_companies  \
0     [{'name': 'Ingenious Film Partners', 'id': 289...   
1     [{'name': 'Walt Disney Pictures', 'id': 2}, {'...   
...                                                 ...   
4801                                                 []   
4802  [{'name': 'rusty bear entertainment', 'id': 87...   

                                   production_countries release_date  \
0     [{'iso_3166_1': 'US', 'name': 'United States o...   2009-12-10   
1     [{'iso_3166_1': 'US', 'name': 'United States o...   2007-05-19   
...                                                 ...          ...   
4801  [{'iso_3166_1': 'US', 'name': 'United States o...   2012-05-03   
4802  [{'iso_3166_1': 'US', 'name': 'United States o...   2005-08-05   

           gross  duration                                   spoken_languages  \
0     2787965087     162.0  [{'iso_639_1': 'en', 'name': 'English'}, {'iso...   
1      961000000     169.0           [{'iso_639_1': 'en', 'name': 'English'}]   
...          ...       ...                                                ...   
4801           0      98.0           [{'iso_639_1': 'en', 'name': 'English'}]   
4802           0      90.0           [{'iso_639_1': 'en', 'name': 'English'}]   

        status                                         tagline  \
0     Released                     Enter the World of Pandora.   
1     Released  At the end of the world, the adventure begins.   
...        ...                                             ...   
4801  Released                        A New Yorker in Shanghai   
4802  Released                                             NaN   

                                   movie_title  vote_average  num_voted_users  \
0                                       Avatar           7.2            11800   
1     Pirates of the Caribbean: At World's End           6.9             4500   
...                                        ...           ...              ...   
4801                          Shanghai Calling           5.7                7   
4802                         My Date with Drew         

In [13]:
df = original_format.copy()
# features_to_remove =['id','original_title','overview', 'movie_title', 'homepage', 'status' , 'plot_keywords', 'spoken_languages', 'gross', 'title_year', 'production_countries','production_companies','tagline', 'vote_average','num_voted_users', 'genres']
features_to_remove =['id','original_title','overview', 'movie_title', 'homepage', 'status' , 'plot_keywords', 'spoken_languages', 'title_year', 'production_countries','production_companies','tagline', 'vote_average','num_voted_users', 'genres']
df.drop(features_to_remove, axis = 1, inplace= True)
df.columns

Index(['budget', 'language', 'popularity', 'release_date', 'gross', 'duration',
       'country', 'company', 'director_name', 'actor_1_name', 'actor_2_name',
       'actor_3_name'],
      dtype='object')

In [14]:
replace_with_zero = ['duration','title_year']

missing_val_cols = list(df.columns[df.isna().any()])
for col in missing_val_cols:
  if col not in replace_with_zero:
    miss_percentage = ((df[col].isna().sum())/4803) * 100 
    print(f'{col} : {str(miss_percentage)}')
    df[col].fillna('Missing', inplace=True)
  else:
    miss_percentage = ((df[col].isna().sum())/4803) * 100 
    print(f'{col} : {str(miss_percentage)}')
    df[col].fillna(df[col].mean(), inplace=True)

df.isna().any()

language : 1.7905475744326462
release_date : 0.020820320632937747
duration : 0.041640641265875494
country : 3.622735790131168
company : 7.30793254216115
director_name : 0.6246096189881324
actor_1_name : 0.8952737872163231
actor_2_name : 1.1034769935457007
actor_3_name : 1.311680199875078


budget          False
language        False
                ...  
actor_2_name    False
actor_3_name    False
Length: 12, dtype: bool

In [15]:
df['release_date'] = pd.to_datetime(df['release_date'].astype(str),errors='coerce')
df['dayofrelease']=df['release_date'].dt.strftime('%A')
df.drop(columns=['release_date'], inplace = True)
df.head(3)

budget  language  popularity       gross  duration  \
0  237000000   English  150.437577  2787965087     162.0   
1  300000000   English  139.082615   961000000     169.0   
2  245000000  Français  107.376788   880674609     148.0   

                    country                  company   director_name  \
0  United States of America  Ingenious Film Partners   James Cameron   
1  United States of America     Walt Disney Pictures  Gore Verbinski   
2            United Kingdom        Columbia Pictures      Sam Mendes   

      actor_1_name     actor_2_name      actor_3_name dayofrelease  
0  Sam Worthington      Zoe Saldana  Sigourney Weaver     Thursday  
1      Johnny Depp    Orlando Bloom   Keira Knightley     Saturday  
2     Daniel Craig  Christoph Waltz       Léa Seydoux       Monday

In [16]:
# Parse the stringified features into their corresponding python objects
from ast import literal_eval

# Function to convert all strings to lower case and strip names of spaces
def clean_data(x):
    if isinstance(x, list):
        return [str.lower(i.replace(" ", "")) for i in x]
    else:
        #Check if director exists. If not, return empty string
        if isinstance(x, str):
            return str.lower(x.replace(" ", ""))
        else:
            return ''


features = ['actor_1_name','actor_2_name','actor_3_name','director_name','country', 'company']
for feature in features:
    df[feature] = df[feature].apply(clean_data)

df

budget language  popularity       gross  duration  \
0     237000000  English  150.437577  2787965087     162.0   
1     300000000  English  139.082615   961000000     169.0   
...         ...      ...         ...         ...       ...   
4801          0  English    0.857008           0      98.0   
4802          0  English    1.929883           0      90.0   

                    country                 company    director_name  \
0     unitedstatesofamerica   ingeniousfilmpartners     jamescameron   
1     unitedstatesofamerica      waltdisneypictures    goreverbinski   
...                     ...                     ...              ...   
4801  unitedstatesofamerica                 missing       danielhsia   
4802  unitedstatesofamerica  rustybearentertainment  brianherzlinger   

        actor_1_name     actor_2_name     actor_3_name dayofrelease  
0     samworthington       zoesaldana  sigourneyweaver     Thursday  
1         johnnydepp     orlandobloom   keiraknightley     Saturday  
...              ...              ...              ...          ...  
4801    danielhenney       elizacoupe       billpaxton     Thursday  
4802   drewbarrymore  brianherzlinger     coreyfeldman       Friday  

[4803 rows x 12 columns]

In [17]:
data_copy = df.copy()

nominal = ['dayofrelease', 'language','actor_1_name','actor_2_name','actor_3_name','director_name','country', 'company']
one_hot = pd.get_dummies(data_copy[nominal])
data_copy.drop(['dayofrelease','language', 'actor_1_name','actor_2_name','actor_3_name','director_name','country', 'company'], axis=1, inplace=True)
data_copy = data_copy.join(one_hot)
data_copy.head()

0   
3                           0                              0   
4                           0                              0   

   company_trianglefilmcorporation  company_tribecafilm  \
0                                0                    0   
1                                0                    0   
2                                0                    0   
3                                0                    0   
4                                0                    0   

   company_tribecaproductions  company_tricastle  \
0                           0                  0   
1                           0                  0   
2                           0                  0   
3                           0                  0   
4                           0                  0   

   company_triggerfishanimation  company_trilogyentertainmentgroup  \
0                             0                                  0   
1                             0                                  0   
2                             0                                  0   
3                             0                                  0   
4                             0                                  0   

   company_tripledproductions  company_tristarpictures  \
0                           0                        0   
1                           0                        0   
2                           0                        0   
3                           0                        0   
4                           0                        0   

   company_tristartelevision  company_triumphantentertainment  \
0                          0                                0   
1                          0                                0   
2                          0                                0   
3                          0                                0   
4                          0                                0   

   company_triumphantpictures  company_tromaentertainment  \
0                           0                           0   
1                           0                           0   
2                           0                           0   
3                           0                           0   
4                           0                           0   

   company_troublemakerstudios  company_trustthemanllc  \
0                            0                       0   
1                            0                       0   
2                            0                       0   
3                            0                       0   
4                            0                       0   

   company_truthandsoulpicturesinc  company_tsproductions  company_tvtokyo  \
0                                0                      0                0   
1                                0                      0                0   
2                                0                      0                0   
3                                0                      0                0   
4                                0                      0                0   

   company_twentiethcenturyfoxfilmcorporation  company_twocamelsfilms  \
0                                           0                       0   
1                                           0                       0   
2                                           0                       0   
3                                           0                       0   
4                                           0                       0   

   company_twostreetsentertainment  company_twotonfilms  \
0                                0                    0   
1                                0                    0   
2                                0                    0   
3                                0                    0   
4                                0                    0   

   company_tylerperrycompany,the  company_typeafilms  comp

In [18]:
# Parse the stringified features into their corresponding python objects
from ast import literal_eval

# Function to convert all strings to lower case and strip names of spaces
def clean_data(x):
    if isinstance(x, list):
        return [str.lower(i.replace(" ", "")) for i in x]
    else:
        #Check if director exists. If not, return empty string
        if isinstance(x, str):
            return str.lower(x.replace(" ", ""))
        else:
            return ''


features = ['actor_1_name','actor_2_name','actor_3_name','director_name','country', 'company']
for feature in features:
    data_copy[feature] = data_copy[feature].apply(clean_data)

data_copy

KeyError: 'actor_1_name'

In [59]:
from sklearn.preprocessing import LabelEncoder

ordinal = ['actor_1_name','actor_2_name','actor_3_name','director_name','country', 'company']
for feature in ordinal:
    data_copy[feature] = data_copy[feature].astype('category')
    data_copy[feature] = data_copy[feature].cat.codes
# pd.set_option('display.max_rows', None)
data_copy

KeyError: 'actor_1_name'

In [60]:
scaler = StandardScaler()

# numerical = df.select_dtypes(include=['int64','float']).copy()
numerical = data_copy.columns[data_copy.dtypes.apply(lambda c: np.issubdtype(c, np.number))]


data_copy[numerical] = scaler.fit_transform(data_copy[numerical])
data_copy.head()

-0.014431   
3                   -0.014431                      -0.014431   
4                   -0.014431                      -0.014431   

   company_trianglefilmcorporation  company_tribecafilm  \
0                        -0.014431            -0.014431   
1                        -0.014431            -0.014431   
2                        -0.014431            -0.014431   
3                        -0.014431            -0.014431   
4                        -0.014431            -0.014431   

   company_tribecaproductions  company_tricastle  \
0                    -0.02041          -0.014431   
1                    -0.02041          -0.014431   
2                    -0.02041          -0.014431   
3                    -0.02041          -0.014431   
4                    -0.02041          -0.014431   

   company_triggerfishanimation  company_trilogyentertainmentgroup  \
0                     -0.014431                          -0.014431   
1                     -0.014431                          -0.014431   
2                     -0.014431                          -0.014431   
3                     -0.014431                          -0.014431   
4                     -0.014431                          -0.014431   

   company_tripledproductions  company_tristarpictures  \
0                   -0.014431                -0.091641   
1                   -0.014431                -0.091641   
2                   -0.014431                -0.091641   
3                   -0.014431                -0.091641   
4                   -0.014431                -0.091641   

   company_tristartelevision  company_triumphantentertainment  \
0                  -0.014431                        -0.014431   
1                  -0.014431                        -0.014431   
2                  -0.014431                        -0.014431   
3                  -0.014431                        -0.014431   
4                  -0.014431                        -0.014431   

   company_triumphantpictures  company_tromaentertainment  \
0                   -0.014431                      -0.025   
1                   -0.014431                      -0.025   
2                   -0.014431                      -0.025   
3                   -0.014431                      -0.025   
4                   -0.014431                      -0.025   

   company_troublemakerstudios  company_trustthemanllc  \
0                    -0.014431               -0.014431   
1                    -0.014431               -0.014431   
2                    -0.014431               -0.014431   
3                    -0.014431               -0.014431   
4                    -0.014431               -0.014431   

   company_truthandsoulpicturesinc  company_tsproductions  company_tvtokyo  \
0                        -0.014431              -0.014431        -0.014431   
1                        -0.014431              -0.014431        -0.014431   
2                        -0.014431              -0.014431        -0.014431   
3                        -0.014431              -0.014431        -0.014431   
4                        -0.014431              -0.014431        -0.014431   

   company_twentiethcenturyfoxfilmcorporation  company_twocamelsfilms  \
0                                   -0.195607               -0.014431   
1                                   -0.195607               -0.014431   
2                                   -0.195607               -0.014431   
3                                   -0.195607               -0.014431   
4                                   -0.195607               -0.014431   

   company_twostreetsentertainment  company_twotonfilms  \
0                        -0.014431            -0.014431   
1                        -0.014431            -0.014431   
2                        -0.014431            -0.014431   
3                        -0.014431            -0.014431   
4                        -0.014431            -0.014431   

   company_tylerperrycompany,the  company_typeafil

In [61]:
data_copy.drop(columns=['gross'], inplace= True)
new_data = pd.concat([data_copy, df['gross']], axis =1)
new_data

...                                ...   
4801                     -0.014431                          -0.014431   
4802                     -0.014431                          -0.014431   

      company_tripledproductions  company_tristarpictures  \
0                      -0.014431                -0.091641   
1                      -0.014431                -0.091641   
...                          ...                      ...   
4801                   -0.014431                -0.091641   
4802                   -0.014431                -0.091641   

      company_tristartelevision  company_triumphantentertainment  \
0                     -0.014431                        -0.014431   
1                     -0.014431                        -0.014431   
...                         ...                              ...   
4801                  -0.014431                        -0.014431   
4802                  -0.014431                        -0.014431   

      company_triumphantpictures  company_tromaentertainment  \
0                      -0.014431                      -0.025   
1                      -0.014431                      -0.025   
...                          ...                         ...   
4801                   -0.014431                      -0.025   
4802                   -0.014431                      -0.025   

      company_troublemakerstudios  company_trustthemanllc  \
0                       -0.014431               -0.014431   
1                       -0.014431               -0.014431   
...                           ...                     ...   
4801                    -0.014431               -0.014431   
4802                    -0.014431               -0.014431   

      company_truthandsoulpicturesinc  company_tsproductions  company_tvtokyo  \
0                           -0.014431              -0.014431        -0.014431   
1                           -0.014431              -0.014431        -0.014431   
...                               ...                    ...              ...   
4801                        -0.014431              -0.014431        -0.014431   
4802                        -0.014431              -0.014431        -0.014431   

      company_twentiethcenturyfoxfilmcorporation  company_twocamelsfilms  \
0                                      -0.195607               -0.014431   
1                                      -0.195607               -0.014431   
...                                          ...                     ...   
4801                                   -0.195607               -0.014431   
4802                                   -0.195607               -0.014431   

      company_twostreetsentertainment  company_twotonfilms  \
0                           -0.014431            -0.014431   
1                           -0.014431            -0.014431   
...                               ...                  ...   
4801                        -0.014431            -0.014431   
4802                        -0.014431            -0.014431   

      company_tylerperrycompany,the  company_typeafilms  \
0                         -0.014431           -0.014431   
1                         -0.014431           -0.014431   
...                             ...                 ...   
4801                      -0.014431           -0.014431   
4802                      -0.014431           -0.014431   

      company_téléfilmcanada  company_ukfilmcouncil  company_ultrafilms  \
0                  -0.028871              -0.032282           -0.014431   
1                  -0.028871              -0.032282           -0.014431   
...                      ...                    ...                 ...   
4801               -0.028871              -0.032282           -0.014431   
4802               -0.028871              -0.032282           -0.014431   

      company_unifiedpictures  company_unitedartists  \
0                   -0.014431              -0.123364   
1                   -0.014431              -0.12

In [62]:
rf_data = data_copy.copy()
rf_data.dtypes

budget                           float64
popularity                       float64
                                  ...   
company_zephyrfilms              float64
company_zininsafilmproduction    float64
Length: 11699, dtype: object

In [63]:
rf_data['Success'] = np.where(df['gross'] >= df['gross'].mean(), 1,0)
# knn_data.drop(columns =['standardised_popularity'], inplace= True)
rf_data

31   
...                            ...                                ...   
4801                     -0.014431                          -0.014431   
4802                     -0.014431                          -0.014431   

      company_tripledproductions  company_tristarpictures  \
0                      -0.014431                -0.091641   
1                      -0.014431                -0.091641   
...                          ...                      ...   
4801                   -0.014431                -0.091641   
4802                   -0.014431                -0.091641   

      company_tristartelevision  company_triumphantentertainment  \
0                     -0.014431                        -0.014431   
1                     -0.014431                        -0.014431   
...                         ...                              ...   
4801                  -0.014431                        -0.014431   
4802                  -0.014431                        -0.014431   

      company_triumphantpictures  company_tromaentertainment  \
0                      -0.014431                      -0.025   
1                      -0.014431                      -0.025   
...                          ...                         ...   
4801                   -0.014431                      -0.025   
4802                   -0.014431                      -0.025   

      company_troublemakerstudios  company_trustthemanllc  \
0                       -0.014431               -0.014431   
1                       -0.014431               -0.014431   
...                           ...                     ...   
4801                    -0.014431               -0.014431   
4802                    -0.014431               -0.014431   

      company_truthandsoulpicturesinc  company_tsproductions  company_tvtokyo  \
0                           -0.014431              -0.014431        -0.014431   
1                           -0.014431              -0.014431        -0.014431   
...                               ...                    ...              ...   
4801                        -0.014431              -0.014431        -0.014431   
4802                        -0.014431              -0.014431        -0.014431   

      company_twentiethcenturyfoxfilmcorporation  company_twocamelsfilms  \
0                                      -0.195607               -0.014431   
1                                      -0.195607               -0.014431   
...                                          ...                     ...   
4801                                   -0.195607               -0.014431   
4802                                   -0.195607               -0.014431   

      company_twostreetsentertainment  company_twotonfilms  \
0                           -0.014431            -0.014431   
1                           -0.014431            -0.014431   
...                               ...                  ...   
4801                        -0.014431            -0.014431   
4802                        -0.014431            -0.014431   

      company_tylerperrycompany,the  company_typeafilms  \
0                         -0.014431           -0.014431   
1                         -0.014431           -0.014431   
...                             ...                 ...   
4801                      -0.014431           -0.014431   
4802                      -0.014431           -0.014431   

      company_téléfilmcanada  company_ukfilmcouncil  company_ultrafilms  \
0                  -0.028871              -0.032282           -0.014431   
1                  -0.028871              -0.032282           -0.014431   
...                      ...                    ...                 ...   
4801               -0.028871              -0.032282           -0.014431   
4802               -0.028871              -0.032282           -0.014431   

      company_unifiedpictures  company_unitedartists  \
0                   -0.014431              -0.123364   
1          

In [99]:
rf_X = rf_data.iloc[:,:-1].values
rf_y = rf_data.iloc[:,11699].values
rf_X

array([[ 5.10718073,  4.05318294,  2.43859561, ..., -0.02887052,
        -0.01443075, -0.01443075],
       [ 6.65440223,  3.69625836,  2.74826337, ..., -0.02887052,
        -0.01443075, -0.01443075],
       [ 5.3036533 ,  2.69963777,  1.81926009, ..., -0.02887052,
        -0.01443075, -0.01443075],
       ...,
       [-0.71331921, -0.63017043,  0.58058904, ..., -0.02887052,
        -0.01443075, -0.01443075],
       [-0.71331921, -0.64863652, -0.39265249, ..., -0.02887052,
        -0.01443075, -0.01443075],
       [-0.71331921, -0.61491246, -0.7465585 , ..., -0.02887052,
        -0.01443075, -0.01443075]])

In [100]:
pca = PCA(n_components = 10)
rf_X = pca.fit_transform(rf_X)
rf_X

array([[-0.76484969,  0.2357998 , -1.6529191 , ..., -0.3773787 ,
         0.46079097,  0.10272931],
       [-0.78433258,  0.26867751, -1.95545422, ..., -0.4591911 ,
         0.3583749 , -0.21880027],
       [-0.85359519,  0.25055432,  0.80661202, ..., -0.80025595,
         0.8484473 ,  0.22868186],
       ...,
       [-2.29142051, -2.94801646, -0.85707587, ..., -2.43561872,
        -3.28813285, -8.50154253],
       [-0.02280296, -0.51165198,  0.30677069, ...,  0.22214875,
        -0.52177681, -0.65631283],
       [ 0.49441769, -0.24672588, -1.56876885, ...,  0.49696191,
         0.20664806,  0.48988106]])

In [101]:
rfX_train, rfX_test, rfy_train, rfy_test = train_test_split(rf_X, rf_y, test_size=0.30)

In [102]:
classifier = RandomForestClassifier(n_estimators=85)
classifier.fit(rfX_train, rfy_train)


RandomForestClassifier(n_estimators=85)

In [103]:
y_pred = classifier.predict(rfX_test)

In [104]:
classifier.score(rfX_test, rfy_test)*100

80.98542678695351

In [105]:
dump(classifier, 'models/gross.joblib')

['models/gross.joblib']

In [24]:
import joblib

model_columns = list(data_copy.columns)
print(model_columns)
joblib.dump(model_columns, 'model_columns')


', 'company_intermediafilms', 'company_internationalproductioncompany', 'company_interscopecommunications', 'company_intrepidpictures', 'company_invinciblepicturescorp.', 'company_irishdreamtime', 'company_irishfilmboard', 'company_irishscreen', 'company_islandfilmgroup', 'company_islandpictures', 'company_isleofmanfilm', 'company_itacafilms', 'company_itcentertainment', 'company_ixtlan', 'company_ixtlanproductions', 'company_iyarafilms', 'company_jackdietzproductions', 'company_jafarpanahifilmproductions', 'company_jcemovies', 'company_jeandoumanianproductions', 'company_jerrybruckheimerfilms', 'company_jerryweintraubproductions', 'company_jerseyfilms', 'company_jewsonfilm', 'company_jfproductions', 'company_jigsawproductions', 'company_jimhensonpictures', 'company_joannaproductions', 'company_jobroproductions&filmfinance', 'company_johnsonproductiongroup', 'company_johnwellsproductions', 'company_journeymanpictures', 'company_junglebookentertainment', 'company_jvcentertainment', 'com

['model_columns']